# Assignment 4: Negamax with Alpha-Beta Pruning and Iterative Deepening

Anurag Kumar

# Table of Contents
* [Assignment 4: Negamax with Alpha-Beta Pruning and Iterative Deepening](#Assignment-4:-Negamax-with-Alpha-Beta-Pruning-and-Iterative-Deepening)
	* [Initial Code](#Initial-Code)
	* [Add moves counter](#Add-moves-counter)
	* [negamaxIDS](#negamaxIDS)
	* [negamaxIDSab](#negamaxIDSab)
	* [Grading](#Grading)
	* [Extra Credit](#Extra-Credit)


In this assignment, I have analysed the advantages of alpha-beta
pruning by implementing Tic-Tac-Toe.

## Initial Code

In [1]:
def negamax(game, depthLeft):
    # If at terminal state or depth limit, return utility value and move None
    if game.isOver() or depthLeft == 0:
        return game.getUtility(), None
    # Find best move and its value from current state
    bestValue = -float('infinity')
    bestMove = None
    for move in game.getMoves():
        # Apply a move to current state
        game.makeMove(move)
        # Use depth-first search to find eventual utility value and back it up.
        #  Negate it because it will come back in context of next player
        value, _ = negamax(game, depthLeft-1)
        # Remove the move from current state, to prepare for trying a different move
        game.unmakeMove(move)
        if value is None:
            continue
        value = - value
        if bestValue is None or value > bestValue:
            # Value for this move is better than moves tried so far from this state.
            bestValue = value
            bestMove = move
    return bestValue, bestMove

In [2]:
class TTT(object):

    def __init__(self):
        self.board = [' ']*9
        self.player = 'X'
        if False:
            self.board = ['X', 'X', ' ', 'X', 'O', 'O', ' ', ' ', ' ']
            self.player = 'O'
        self.playerLookAHead = self.player
        self.movesExplored = 0
        self.winningValue = 1

    def locations(self, c):
        return [i for i, mark in enumerate(self.board) if mark == c]

    def getMoves(self):
        moves = self.locations(' ')
        return moves

    def getUtility(self):
        whereX = self.locations('X')
        whereO = self.locations('O')
        wins = [[0, 1, 2], [3, 4, 5], [6, 7, 8],
                [0, 3, 6], [1, 4, 7], [2, 5, 8],
                [0, 4, 8], [2, 4, 6]]
        isXWon = any([all([wi in whereX for wi in w]) for w in wins])
        isOWon = any([all([wi in whereO for wi in w]) for w in wins])
        if isXWon:
            return 1 if self.playerLookAHead is 'X' else -1
        elif isOWon:
            return 1 if self.playerLookAHead is 'O' else -1
        elif ' ' not in self.board:
            return 0
        else:
            return None  ########################################################## CHANGED FROM -0.1

    def isOver(self):
        return self.getUtility() is not None

    def makeMove(self, move):
        self.movesExplored+=1
        self.board[move] = self.playerLookAHead
        self.playerLookAHead = 'X' if self.playerLookAHead == 'O' else 'O'

    def changePlayer(self):
        self.player = 'X' if self.player == 'O' else 'O'
        self.playerLookAHead = self.player

    def unmakeMove(self, move):
        self.board[move] = ' '
        self.playerLookAHead = 'X' if self.playerLookAHead == 'O' else 'O'

    def __str__(self):
        s = '{}|{}|{}\n-----\n{}|{}|{}\n-----\n{}|{}|{}'.format(*self.board)
        return s
    
    def getNumberMovesExplored(self):
        return self.movesExplored
    
    def getWinningValue(self):
        return self.winningValue

The following function `playGame` uses *negamax* to find the best move for
Player X, but Player O, the opponent, is using function *opponent*
that follows the silly strategy of playing in the first open position.

In [3]:
def opponent(board):
    return board.index(' ')

def playGame(game,opponent,depthLimit):
    print(game)
    while not game.isOver():
        score,move = negamax(game,depthLimit)
        if move == None :
            print('move is None. Stopping.')
            break
        game.makeMove(move)
        print('Player', game.player, 'to', move, 'for score' ,score)
        print(game)
        if not game.isOver():
            game.changePlayer()
            opponentMove = opponent(game.board)
            game.makeMove(opponentMove)
            print('Player', game.player, 'to', opponentMove)   ### FIXED ERROR IN THIS LINE!
            print(game)
            game.changePlayer()

In [4]:
game = TTT()
playGame(game,opponent,20)
game.getNumberMovesExplored()

 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 0
X| | 
-----
 | | 
-----
 | | 
Player O to 1
X|O| 
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X|O| 
-----
X| | 
-----
 | | 
Player O to 2
X|O|O
-----
X| | 
-----
 | | 
Player X to 4 for score 1
X|O|O
-----
X|X| 
-----
 | | 
Player O to 5
X|O|O
-----
X|X|O
-----
 | | 
Player X to 6 for score 1
X|O|O
-----
X|X|O
-----
X| | 


558334

## Added a counter to know the number of nodes explored

We can evaluate the efficiency of the search by keepting track of the number of nodes explored, which is the same as the number of moves explored, during a game. I did this by adding a counter named `movesExplored` to the `TTT` constructor where it is initialized to 0 and increment the counter in the `TTT.makeMove` method. And I also added a method `ttt.getNumberMovesExplored()` to get its current value.  So

    print('Number of moves explored', game.getMovesExplored())
    
will print the number of moves explored.

## negamaxIDS 

<font color='red'>UPDATED Oct 4</font>

I wrote a new function named `negamaxIDS` that performs an iterative deepening negamax search by replacing the first line in the `while` loop of `playGame` with

        score,move = negamaxIDS(game,depthLimit)
        
where `depthLimit` is now the maximum depth and multiple `negamax` searches are performed for depth limits of $1, 2, \ldots,$ maximum depth.


For Tic-Tac-Toe, we can stop as soon as a call to `negamax` returns a winning move.  This will have a value of 1 for Tic-Tac-Toe.  To keep our `negamaxIDS` function general, I added a method called `getWinningValue` to the `TTT` class that just returns 1.  Then `negamaxIDS` calls `game.getWinningValue()` to determine the value of a winning move for this game.  If the maximum depth is reached and no winning move has been found, return the best move found over all depth limts.

In [5]:
def negamaxIDS(game, depthLimit):
     # If at terminal state or depth limit, return utility value and move None
    if game.isOver() or depthLimit == 0:
        return game.getUtility(), None
    # Find best move and its value from current state
    bestValue = -float('infinity')
    bestMove = None
    for depth in range(depthLimit):
        value, move = negamax(game, depth)
        #print('value: ',value)
        if value is None:
            continue
        #value = -value
        if value> bestValue and value!=float('infinity'):
            bestValue = value
            bestMove = move
        if bestValue == game.getWinningValue():
            return bestValue, bestMove
    return bestValue, bestMove

In [6]:
def opponent(board):
    return board.index(' ')

def playGameIDS(game,opponent,depthLimit):
    print(game)
    while not game.isOver():
        score,move = negamaxIDS(game,depthLimit)
        if move == None :
            print('move is None. Stopping.')
            break
        game.makeMove(move)
        print('Player', game.player, 'to', move, 'for score' ,score)
        print(game)
        if not game.isOver():
            game.changePlayer()
            opponentMove = opponent(game.board)
            game.makeMove(opponentMove)
            print('Player', game.player, 'to', opponentMove)   ### FIXED ERROR IN THIS LINE!
            print(game)
            game.changePlayer()

In [7]:
game = TTT()
playGameIDS(game, opponent, 20)
game.getNumberMovesExplored()

 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 1
X|O| 
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X|O| 
-----
X| | 
-----
 | | 
Player O to 2
X|O|O
-----
X| | 
-----
 | | 
Player X to 6 for score 1
X|O|O
-----
X| | 
-----
X| | 


744695

## negamaxIDSab

This is another new function `negamaxIDSab` that i created by duplicating `negamaxIDS` and adding the code to implement alpha-beta pruning.

In [8]:
''' This is the modified version of the negamax given in the assignment. It includes two new parameters 'a' and 'b' which
represents alpha and beta values for implementing alpha-beta prunning.
'''
def negamaxAB(game, depthLeft, a, b):
    # If at terminal state or depth limit, return utility value and move None
    if game.isOver() or depthLeft == 0:
        return game.getUtility(), None
    # Find best move and its value from current state
    bestValue = -float('infinity')
    bestMove = None
    for move in game.getMoves():
        # Apply a move to current state
        game.makeMove(move)
        # Use depth-first search to find eventual utility value and back it up.
        #  Negate it because it will come back in context of next player
        value, _ = negamaxAB(game, depthLeft-1, -b, -a) # Negating and swapping the 'a' and 'b' values
        # Remove the move from current state, to prepare for trying a different move
        game.unmakeMove(move)
        if value is None:
            continue
        value = - value
        if value > bestValue:
            # Value for this move is better than moves tried so far from this state.
            bestValue = value
            bestMove = move
            a = value if value > a else a # Updating the current alpha value to the best value
        if bestValue >= b: # Prunning all the state from which we know 'X' has no chance of winning
            return bestValue, bestMove
    return bestValue, bestMove

In [9]:
def negamaxIDSab(game, depthLimit):
     # If at terminal state or depth limit, return utility value and move None
    if game.isOver() or depthLimit == 0:
        return game.getUtility(), None
    # Find best move and its value from current state
    bestValue = -float('infinity')
    bestMove = None
    a = -float('infinity')
    b = float('infinity')
    for depth in range(depthLimit):
        value, move = negamaxAB(game, depth, a, b)
        #print('value: ',value)
        if value is None:
            continue
        #value = -value
        if value> bestValue and value!=float('infinity'):
            bestValue = value
            bestMove = move
        if bestValue == game.getWinningValue():
            return bestValue, bestMove
    return bestValue, bestMove

In [10]:
def opponent(board):
    return board.index(' ')

def playGameIDSab(game,opponent,depthLimit):
    print(game)
    while not game.isOver():
        score,move = negamaxIDSab(game,depthLimit)
        if move == None :
            print('move is None. Stopping.')
            break
        game.makeMove(move)
        print('Player', game.player, 'to', move, 'for score' ,score)
        print(game)
        if not game.isOver():
            game.changePlayer()
            opponentMove = opponent(game.board)
            game.makeMove(opponentMove)
            print('Player', game.player, 'to', opponentMove)   ### FIXED ERROR IN THIS LINE!
            print(game)
            game.changePlayer()

In [11]:
game = TTT()
playGameIDSab(game, opponent, 20)
game.getNumberMovesExplored()

 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 1
X|O| 
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X|O| 
-----
X| | 
-----
 | | 
Player O to 2
X|O|O
-----
X| | 
-----
 | | 
Player X to 6 for score 1
X|O|O
-----
X| | 
-----
X| | 


20804

## playGames

This function duplicates the game playing loop so three complete tic-tac-toe games can be played. For the first game, I used `negamax`. For the second game, I used `negamaxIDS`.  For the third game, I used `negamaxIDSab`.  At the end of each game, it prints the number of X's in the final board, the number moves explored, the depth of the game which is the number of moves made by X and O, and the effective branching factor.  When we run `playGames` we can see the tic-tac-toe positions after each move and, after all games are done, a line for each game like the following lines, which were <font color='red'>UPDATED Oct 5</font>.

    negamax made 4 moves. 558334 moves explored for ebf(558334, 7) of 6.46
    negamaxIDS made 3 moves. 744695 moves explored for ebf(744695, 5) of 14.73
    negamaxIDSab made 3 moves 20804 moves explored for ebf(20804, 5) of 7.09
 
The value of the depth is the total number of moves made by X and by O during the search. I calculated this by just counting the number of X's and O's in the final board.

#### The ebf() is borrowed from Assignment 3

In [12]:
def cal(b, d):
    if b!=1 and d!=1:
        return (1-b**(d+1))/(1-b)
    if d==1:
        return 1+b

In [13]:
def ebf(numberNodes, depth, precision=0.001):
    n = numberNodes
    d = depth
    a = n*precision
    low = 1
    high = n
    while True:
        if n==0:
            return 0.000
        if d==0:
            return 1
        b = (high+low)/2
        y_b = cal(b,d)
        if y_b<n:
            low = b
        elif y_b>n:
            high = b
        if abs(n-y_b)<a:
            return round(b,2)

In [14]:
def opponent(board):
    return board.index(' ')

def playGames(opponent, depthLimit):
    print('negamax:')
    game1 = TTT()
    playGame(game1,opponent,depthLimit)
    print()
    #game.getNumberMovesExplored()
    print('negamaxIDS:')
    game2 = TTT()
    playGameIDS(game2,opponent,depthLimit)
    print()
    #game.getNumberMovesExplored()
    print('negamaxIDSab:')
    game3 = TTT()
    playGameIDSab(game3,opponent,depthLimit)
    #game.getNumberMovesExplored()
    print('negamax made {} moves. {} moves explored for ebf({}, {}) of {}'.format
          (game1.board.count('X'),game1.getNumberMovesExplored(),game1.getNumberMovesExplored(),
           game1.board.count('X')+game1.board.count('O'),
           ebf(game1.getNumberMovesExplored(),game1.board.count('X')+game1.board.count('O'))))
    print('negamaxIDS made {} moves. {} moves explored for ebf({}, {}) of {}'.format
          (game2.board.count('X'),game2.getNumberMovesExplored(),game2.getNumberMovesExplored(),
           game2.board.count('X')+game2.board.count('O'),
           ebf(game2.getNumberMovesExplored(),game2.board.count('X')+game2.board.count('O'))))
    print('negamaxIDSab made {} moves. {} moves explored for ebf({}, {}) of {}'.format
          (game3.board.count('X'),game3.getNumberMovesExplored(),game3.getNumberMovesExplored(),
           game3.board.count('X')+game3.board.count('O'),
           ebf(game3.getNumberMovesExplored(),game3.board.count('X')+game3.board.count('O'))))

Here are some example results.

In [15]:
playGames(opponent, 10)

negamax:
 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 0
X| | 
-----
 | | 
-----
 | | 
Player O to 1
X|O| 
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X|O| 
-----
X| | 
-----
 | | 
Player O to 2
X|O|O
-----
X| | 
-----
 | | 
Player X to 4 for score 1
X|O|O
-----
X|X| 
-----
 | | 
Player O to 5
X|O|O
-----
X|X|O
-----
 | | 
Player X to 6 for score 1
X|O|O
-----
X|X|O
-----
X| | 

negamaxIDS:
 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 1
X|O| 
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X|O| 
-----
X| | 
-----
 | | 
Player O to 2
X|O|O
-----
X| | 
-----
 | | 
Player X to 6 for score 1
X|O|O
-----
X| | 
-----
X| | 

negamaxIDSab:
 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 1
X|O| 
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X|O| 
-----
X| | 
-----
 | | 
Player O to 2
X|O|O
-----
X| | 
-----
 | | 
Player X to 6 for score 1
X|O|O
-----
X| | 
-----
X| | 
negam

## Extra Credit 

Earn one extra credit point for each of the following.

  - Implement another game and repeat the above steps.

  - Implement a random move chooser as the opponent (Player O) and determine how many times Player X can win against this opponent as an average over multiple games.

In [17]:
import random

def opponentA(board):                            # This is an opponent which plays 'O' at any random loccation from 
    n = []                                       # a set of all possible valid moves
    for i in range(len(board)):
        if board[i]==' ':
            n.append(i)
    
    #print(n)
    #print(random.choice(n))
    return random.choice(n)

### The block below conatins the output for negamax being implemented 100 times

In [18]:
countX = 0                                    # This counts the number of times 'X' won the game
countO = 0                                    # This counts the number of times 'O' won the game
countD = 0                                    # This counts the number of times the game ended in a draw
for i in range(100):
    game = TTT()
    playGame(game, opponentA, 20)
    if game.getUtility()== -1:
        countX += 1
    elif game.getUtility()== 1:
        countO += 1
    print()
    print()
    print()
print('countX: ',countX)
print('countO: ',countO)
print('countD: ',100-countX-countO)

 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 0
X| | 
-----
 | | 
-----
 | | 
Player O to 8
X| | 
-----
 | | 
-----
 | |O
Player X to 2 for score 1
X| |X
-----
 | | 
-----
 | |O
Player O to 6
X| |X
-----
 | | 
-----
O| |O
Player X to 1 for score 1
X|X|X
-----
 | | 
-----
O| |O



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 0
X| | 
-----
 | | 
-----
 | | 
Player O to 5
X| | 
-----
 | |O
-----
 | | 
Player X to 2 for score 1
X| |X
-----
 | |O
-----
 | | 
Player O to 6
X| |X
-----
 | |O
-----
O| | 
Player X to 1 for score 1
X|X|X
-----
 | |O
-----
O| | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 0
X| | 
-----
 | | 
-----
 | | 
Player O to 4
X| | 
-----
 |O| 
-----
 | | 
Player X to 1 for score 0
X|X| 
-----
 |O| 
-----
 | | 
Player O to 2
X|X|O
-----
 |O| 
-----
 | | 
Player X to 6 for score 0
X|X|O
-----
 |O| 
-----
X| | 
Player O to 7
X|X|O
-----
 |O| 
-----
X|O| 
Player X to 3 for score 1
X|X|O
-----
X|O| 
-----
X|O| 



 | | 
-----
 | | 
-----
 | | 
Pla

Player X to 2 for score 1
X| |X
-----
 | |O
-----
 | | 
Player O to 1
X|O|X
-----
 | |O
-----
 | | 
Player X to 4 for score 1
X|O|X
-----
 |X|O
-----
 | | 
Player O to 3
X|O|X
-----
O|X|O
-----
 | | 
Player X to 6 for score 1
X|O|X
-----
O|X|O
-----
X| | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 0
X| | 
-----
 | | 
-----
 | | 
Player O to 4
X| | 
-----
 |O| 
-----
 | | 
Player X to 1 for score 0
X|X| 
-----
 |O| 
-----
 | | 
Player O to 8
X|X| 
-----
 |O| 
-----
 | |O
Player X to 2 for score 1
X|X|X
-----
 |O| 
-----
 | |O



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 0
X| | 
-----
 | | 
-----
 | | 
Player O to 1
X|O| 
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X|O| 
-----
X| | 
-----
 | | 
Player O to 4
X|O| 
-----
X|O| 
-----
 | | 
Player X to 6 for score 1
X|O| 
-----
X|O| 
-----
X| | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 0
X| | 
-----
 | | 
-----
 | | 
Player O to 8
X| | 
-----
 | | 
-----
 | |O
Player X to 2 for score 1
X| |X
-

Player X to 1 for score 1
X|X| 
-----
 | | 
-----
O| | 
Player O to 4
X|X| 
-----
 |O| 
-----
O| | 
Player X to 2 for score 1
X|X|X
-----
 |O| 
-----
O| | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 0
X| | 
-----
 | | 
-----
 | | 
Player O to 2
X| |O
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X| |O
-----
X| | 
-----
 | | 
Player O to 4
X| |O
-----
X|O| 
-----
 | | 
Player X to 6 for score 1
X| |O
-----
X|O| 
-----
X| | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 0
X| | 
-----
 | | 
-----
 | | 
Player O to 1
X|O| 
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X|O| 
-----
X| | 
-----
 | | 
Player O to 4
X|O| 
-----
X|O| 
-----
 | | 
Player X to 6 for score 1
X|O| 
-----
X|O| 
-----
X| | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 0
X| | 
-----
 | | 
-----
 | | 
Player O to 8
X| | 
-----
 | | 
-----
 | |O
Player X to 2 for score 1
X| |X
-----
 | | 
-----
 | |O
Player O to 6
X| |X
-----
 | | 
-----
O| |O
Player X to 1 for score 1
X|X|X
-

Player X to 3 for score 1
X| |O
-----
X| | 
-----
 | | 
Player O to 7
X| |O
-----
X| | 
-----
 |O| 
Player X to 4 for score 1
X| |O
-----
X|X| 
-----
 |O| 
Player O to 8
X| |O
-----
X|X| 
-----
 |O|O
Player X to 5 for score 1
X| |O
-----
X|X|X
-----
 |O|O



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 0
X| | 
-----
 | | 
-----
 | | 
Player O to 5
X| | 
-----
 | |O
-----
 | | 
Player X to 2 for score 1
X| |X
-----
 | |O
-----
 | | 
Player O to 1
X|O|X
-----
 | |O
-----
 | | 
Player X to 4 for score 1
X|O|X
-----
 |X|O
-----
 | | 
Player O to 7
X|O|X
-----
 |X|O
-----
 |O| 
Player X to 3 for score 1
X|O|X
-----
X|X|O
-----
 |O| 
Player O to 6
X|O|X
-----
X|X|O
-----
O|O| 
Player X to 8 for score 1
X|O|X
-----
X|X|O
-----
O|O|X



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 0
X| | 
-----
 | | 
-----
 | | 
Player O to 2
X| |O
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X| |O
-----
X| | 
-----
 | | 
Player O to 8
X| |O
-----
X| | 
-----
 | |O
Player X to 5 for scor

### The block below conatins the output for negamaxIDS being implemented 100 times

In [19]:
countX = 0                                    # This counts the number of times 'X' won the game
countO = 0                                    # This counts the number of times 'O' won the game
countD = 0                                    # This counts the number of times the game ended in a draw
for i in range(100):
    game = TTT()
    playGameIDS(game, opponentA, 20)
    if game.getUtility()== -1:
        countX += 1
    elif game.getUtility()== 1:
        countO += 1
    print()
    print()
    print()
print('countX: ',countX)
print('countO: ',countO)
print('countD: ',100-countX-countO)

 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 1
X|O| 
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X|O| 
-----
X| | 
-----
 | | 
Player O to 4
X|O| 
-----
X|O| 
-----
 | | 
Player X to 6 for score 1
X|O| 
-----
X|O| 
-----
X| | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 2
X| |O
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X| |O
-----
X| | 
-----
 | | 
Player O to 7
X| |O
-----
X| | 
-----
 |O| 
Player X to 6 for score 1
X| |O
-----
X| | 
-----
X|O| 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 2
X| |O
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X| |O
-----
X| | 
-----
 | | 
Player O to 4
X| |O
-----
X|O| 
-----
 | | 
Player X to 6 for score 1
X| |O
-----
X|O| 
-----
X| | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 1
X|O| 
-----
 | | 
-----
 | | 
Pla

Player X to 3 for score 1
X|O| 
-----
X| | 
-----
 | | 
Player O to 8
X|O| 
-----
X| | 
-----
 | |O
Player X to 6 for score 1
X|O| 
-----
X| | 
-----
X| |O



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 8
X| | 
-----
 | | 
-----
 | |O
Player X to 2 for score 1
X| |X
-----
 | | 
-----
 | |O
Player O to 3
X| |X
-----
O| | 
-----
 | |O
Player X to 1 for score 1
X|X|X
-----
O| | 
-----
 | |O



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 4
X| | 
-----
 |O| 
-----
 | | 
Player X to 1 for score 1
X|X| 
-----
 |O| 
-----
 | | 
Player O to 2
X|X|O
-----
 |O| 
-----
 | | 
Player X to 6 for score 1
X|X|O
-----
 |O| 
-----
X| | 
Player O to 3
X|X|O
-----
O|O| 
-----
X| | 
Player X to 5 for score 0
X|X|O
-----
O|O|X
-----
X| | 
Player O to 8
X|X|O
-----
O|O|X
-----
X| |O
Player X to 7 for score 0
X|X|O
-----
O|O|X
-----
X|X|O



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-

Player X to 2 for score 1
X| |X
-----
 | |O
-----
 | | 
Player O to 6
X| |X
-----
 | |O
-----
O| | 
Player X to 1 for score 1
X|X|X
-----
 | |O
-----
O| | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 1
X|O| 
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X|O| 
-----
X| | 
-----
 | | 
Player O to 8
X|O| 
-----
X| | 
-----
 | |O
Player X to 6 for score 1
X|O| 
-----
X| | 
-----
X| |O



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 6
X| | 
-----
 | | 
-----
O| | 
Player X to 1 for score 1
X|X| 
-----
 | | 
-----
O| | 
Player O to 5
X|X| 
-----
 | |O
-----
O| | 
Player X to 2 for score 1
X|X|X
-----
 | |O
-----
O| | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 2
X| |O
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X| |O
-----
X| | 
-----
 | | 
Player O to 8
X| |O
-----
X| | 
-----
 | |O
Player X to 6 for score 1
X| |O
-

Player X to 3 for score 1
X| |O
-----
X| | 
-----
 | | 
Player O to 5
X| |O
-----
X| |O
-----
 | | 
Player X to 6 for score 1
X| |O
-----
X| |O
-----
X| | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 5
X| | 
-----
 | |O
-----
 | | 
Player X to 2 for score 1
X| |X
-----
 | |O
-----
 | | 
Player O to 7
X| |X
-----
 | |O
-----
 |O| 
Player X to 1 for score 1
X|X|X
-----
 | |O
-----
 |O| 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 8
X| | 
-----
 | | 
-----
 | |O
Player X to 2 for score 1
X| |X
-----
 | | 
-----
 | |O
Player O to 3
X| |X
-----
O| | 
-----
 | |O
Player X to 1 for score 1
X|X|X
-----
O| | 
-----
 | |O



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 6
X| | 
-----
 | | 
-----
O| | 
Player X to 1 for score 1
X|X| 
-----
 | | 
-----
O| | 
Player O to 7
X|X| 
-----
 | | 
-----
O|O| 
Player X to 2 for score 1
X|X|X
-

### The block below conatins the output for negamaxIDSab being implemented 100 times

In [20]:
countX = 0                                    # This counts the number of times 'X' won the game
countO = 0                                    # This counts the number of times 'O' won the game
countD = 0                                    # This counts the number of times the game ended in a draw
for i in range(100):
    game = TTT()
    playGameIDSab(game, opponentA, 20)
    if game.getUtility()== -1:
        countX += 1
    elif game.getUtility()== 1:
        countO += 1
    print()
    print()
    print()
print('countX: ',countX)
print('countO: ',countO)
print('countD: ',100-countX-countO)

 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 2
X| |O
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X| |O
-----
X| | 
-----
 | | 
Player O to 5
X| |O
-----
X| |O
-----
 | | 
Player X to 6 for score 1
X| |O
-----
X| |O
-----
X| | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 5
X| | 
-----
 | |O
-----
 | | 
Player X to 2 for score 1
X| |X
-----
 | |O
-----
 | | 
Player O to 1
X|O|X
-----
 | |O
-----
 | | 
Player X to 4 for score 1
X|O|X
-----
 |X|O
-----
 | | 
Player O to 6
X|O|X
-----
 |X|O
-----
O| | 
Player X to 8 for score 1
X|O|X
-----
 |X|O
-----
O| |X



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 4
X| | 
-----
 |O| 
-----
 | | 
Player X to 1 for score 1
X|X| 
-----
 |O| 
-----
 | | 
Player O to 3
X|X| 
-----
O|O| 
-----
 | | 
Player X to 2 for score 1
X|X|X
-----
O|O| 
-----
 | | 



 | | 
-----
 | | 
-----
 | | 
Pla

Player X to 1 for score 1
X|X| 
-----
O| | 
-----
 | | 
Player O to 6
X|X| 
-----
O| | 
-----
O| | 
Player X to 2 for score 1
X|X|X
-----
O| | 
-----
O| | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 7
X| | 
-----
 | | 
-----
 |O| 
Player X to 2 for score 1
X| |X
-----
 | | 
-----
 |O| 
Player O to 3
X| |X
-----
O| | 
-----
 |O| 
Player X to 1 for score 1
X|X|X
-----
O| | 
-----
 |O| 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 4
X| | 
-----
 |O| 
-----
 | | 
Player X to 1 for score 1
X|X| 
-----
 |O| 
-----
 | | 
Player O to 6
X|X| 
-----
 |O| 
-----
O| | 
Player X to 2 for score 1
X|X|X
-----
 |O| 
-----
O| | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 8
X| | 
-----
 | | 
-----
 | |O
Player X to 2 for score 1
X| |X
-----
 | | 
-----
 | |O
Player O to 7
X| |X
-----
 | | 
-----
 |O|O
Player X to 1 for score 1
X|X|X
-

Player X to 2 for score 1
X| |X
-----
 | | 
-----
 | |O
Player O to 4
X| |X
-----
 |O| 
-----
 | |O
Player X to 1 for score 1
X|X|X
-----
 |O| 
-----
 | |O



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 5
X| | 
-----
 | |O
-----
 | | 
Player X to 2 for score 1
X| |X
-----
 | |O
-----
 | | 
Player O to 8
X| |X
-----
 | |O
-----
 | |O
Player X to 1 for score 1
X|X|X
-----
 | |O
-----
 | |O



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 5
X| | 
-----
 | |O
-----
 | | 
Player X to 2 for score 1
X| |X
-----
 | |O
-----
 | | 
Player O to 4
X| |X
-----
 |O|O
-----
 | | 
Player X to 1 for score 1
X|X|X
-----
 |O|O
-----
 | | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 8
X| | 
-----
 | | 
-----
 | |O
Player X to 2 for score 1
X| |X
-----
 | | 
-----
 | |O
Player O to 4
X| |X
-----
 |O| 
-----
 | |O
Player X to 1 for score 1
X|X|X
-

We can see from the the results of running these algorithms for 100 iterations the winning percentage for 'X' are as follows:
<ul><b>
    <li>negamax      : 99</li>
    <li>negamaxIDS   : 99</li>
    <li>negamaxIDSab : 100</li>
</b></ul>
We can also conclude that 'X' never loses in worst case 'X' forces the game to end in a draw.

### The block below conatins the output for negamaxIDSab being implemented 10000 times

In [25]:
countX = 0                                    # This counts the number of times 'X' won the game
countO = 0                                    # This counts the number of times 'O' won the game
countD = 0                                    # This counts the number of times the game ended in a draw
for i in range(10000):
    game = TTT()
    playGameIDSab(game, opponentA, 20)
    if game.getUtility()== -1:
        countX += 1
    elif game.getUtility()== 1:
        countO += 1
    print()
    print()
    print()
print('countX: ',countX)
print('countO: ',countO)
print('countD: ',10000-countX-countO)

 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 7
X| | 
-----
 | | 
-----
 |O| 
Player X to 2 for score 1
X| |X
-----
 | | 
-----
 |O| 
Player O to 1
X|O|X
-----
 | | 
-----
 |O| 
Player X to 4 for score 1
X|O|X
-----
 |X| 
-----
 |O| 
Player O to 8
X|O|X
-----
 |X| 
-----
 |O|O
Player X to 6 for score 1
X|O|X
-----
 |X| 
-----
X|O|O



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 5
X| | 
-----
 | |O
-----
 | | 
Player X to 2 for score 1
X| |X
-----
 | |O
-----
 | | 
Player O to 1
X|O|X
-----
 | |O
-----
 | | 
Player X to 4 for score 1
X|O|X
-----
 |X|O
-----
 | | 
Player O to 7
X|O|X
-----
 |X|O
-----
 |O| 
Player X to 6 for score 1
X|O|X
-----
 |X|O
-----
X|O| 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 5
X| | 
-----
 | |O
-----
 | | 
Player X to 2 for score 1
X| |X
-----
 | |O
-----
 | | 
Player O to 7
X| |X
-----
 | |O
----

Player X to 1 for score 1
X|X| 
-----
 |O| 
-----
 | | 
Player O to 2
X|X|O
-----
 |O| 
-----
 | | 
Player X to 6 for score 1
X|X|O
-----
 |O| 
-----
X| | 
Player O to 3
X|X|O
-----
O|O| 
-----
X| | 
Player X to 5 for score 0
X|X|O
-----
O|O|X
-----
X| | 
Player O to 8
X|X|O
-----
O|O|X
-----
X| |O
Player X to 7 for score 0
X|X|O
-----
O|O|X
-----
X|X|O



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 6
X| | 
-----
 | | 
-----
O| | 
Player X to 1 for score 1
X|X| 
-----
 | | 
-----
O| | 
Player O to 5
X|X| 
-----
 | |O
-----
O| | 
Player X to 2 for score 1
X|X|X
-----
 | |O
-----
O| | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 2
X| |O
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X| |O
-----
X| | 
-----
 | | 
Player O to 5
X| |O
-----
X| |O
-----
 | | 
Player X to 6 for score 1
X| |O
-----
X| |O
-----
X| | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-

Player X to 1 for score 1
X|X| 
-----
O| | 
-----
 | | 
Player O to 8
X|X| 
-----
O| | 
-----
 | |O
Player X to 2 for score 1
X|X|X
-----
O| | 
-----
 | |O



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 2
X| |O
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X| |O
-----
X| | 
-----
 | | 
Player O to 7
X| |O
-----
X| | 
-----
 |O| 
Player X to 6 for score 1
X| |O
-----
X| | 
-----
X|O| 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 5
X| | 
-----
 | |O
-----
 | | 
Player X to 2 for score 1
X| |X
-----
 | |O
-----
 | | 
Player O to 4
X| |X
-----
 |O|O
-----
 | | 
Player X to 1 for score 1
X|X|X
-----
 |O|O
-----
 | | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 8
X| | 
-----
 | | 
-----
 | |O
Player X to 2 for score 1
X| |X
-----
 | | 
-----
 | |O
Player O to 3
X| |X
-----
O| | 
-----
 | |O
Player X to 1 for score 1
X|X|X
-

Player X to 2 for score 1
X| |X
-----
 | | 
-----
 | |O
Player O to 5
X| |X
-----
 | |O
-----
 | |O
Player X to 1 for score 1
X|X|X
-----
 | |O
-----
 | |O



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 6
X| | 
-----
 | | 
-----
O| | 
Player X to 1 for score 1
X|X| 
-----
 | | 
-----
O| | 
Player O to 3
X|X| 
-----
O| | 
-----
O| | 
Player X to 2 for score 1
X|X|X
-----
O| | 
-----
O| | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 2
X| |O
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X| |O
-----
X| | 
-----
 | | 
Player O to 6
X| |O
-----
X| | 
-----
O| | 
Player X to 4 for score 1
X| |O
-----
X|X| 
-----
O| | 
Player O to 7
X| |O
-----
X|X| 
-----
O|O| 
Player X to 5 for score 1
X| |O
-----
X|X|X
-----
O|O| 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 6
X| | 
-----
 | | 
-----
O| | 
Player X to 1 for score 1
X|X| 
-

Player X to 1 for score 1
X|X| 
-----
O| | 
-----
 | | 
Player O to 5
X|X| 
-----
O| |O
-----
 | | 
Player X to 2 for score 1
X|X|X
-----
O| |O
-----
 | | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 7
X| | 
-----
 | | 
-----
 |O| 
Player X to 2 for score 1
X| |X
-----
 | | 
-----
 |O| 
Player O to 8
X| |X
-----
 | | 
-----
 |O|O
Player X to 1 for score 1
X|X|X
-----
 | | 
-----
 |O|O



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 2
X| |O
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X| |O
-----
X| | 
-----
 | | 
Player O to 4
X| |O
-----
X|O| 
-----
 | | 
Player X to 6 for score 1
X| |O
-----
X|O| 
-----
X| | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 3
X| | 
-----
O| | 
-----
 | | 
Player X to 1 for score 1
X|X| 
-----
O| | 
-----
 | | 
Player O to 5
X|X| 
-----
O| |O
-----
 | | 
Player X to 2 for score 1
X|X|X
-

...

Player O to 8
X|O| 
-----
X| | 
-----
 | |O
Player X to 6 for score 1
X|O| 
-----
X| | 
-----
X| |O



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 8
X| | 
-----
 | | 
-----
 | |O
Player X to 2 for score 1
X| |X
-----
 | | 
-----
 | |O
Player O to 6
X| |X
-----
 | | 
-----
O| |O
Player X to 1 for score 1
X|X|X
-----
 | | 
-----
O| |O



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 2
X| |O
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X| |O
-----
X| | 
-----
 | | 
Player O to 6
X| |O
-----
X| | 
-----
O| | 
Player X to 4 for score 1
X| |O
-----
X|X| 
-----
O| | 
Player O to 1
X|O|O
-----
X|X| 
-----
O| | 
Player X to 5 for score 1
X|O|O
-----
X|X|X
-----
O| | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 4
X| | 
-----
 |O| 
-----
 | | 
Player X to 1 for score 1
X|X| 
-----
 |O| 
-----
 | | 
Player O to 5
X|X| 
-----
 |O|O
-

X|X| 
-----
O| | 
-----
 | | 
Player O to 4
X|X| 
-----
O|O| 
-----
 | | 
Player X to 2 for score 1
X|X|X
-----
O|O| 
-----
 | | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 5
X| | 
-----
 | |O
-----
 | | 
Player X to 2 for score 1
X| |X
-----
 | |O
-----
 | | 
Player O to 4
X| |X
-----
 |O|O
-----
 | | 
Player X to 1 for score 1
X|X|X
-----
 |O|O
-----
 | | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 8
X| | 
-----
 | | 
-----
 | |O
Player X to 2 for score 1
X| |X
-----
 | | 
-----
 | |O
Player O to 6
X| |X
-----
 | | 
-----
O| |O
Player X to 1 for score 1
X|X|X
-----
 | | 
-----
O| |O



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 3
X| | 
-----
O| | 
-----
 | | 
Player X to 1 for score 1
X|X| 
-----
O| | 
-----
 | | 
Player O to 2
X|X|O
-----
O| | 
-----
 | | 
Player X to 4 for score 1
X|X|O
-----
O|X| 
-----
 | | 
Pla

Player O to 4
X| |X
-----
 |O|O
-----
 | | 
Player X to 1 for score 1
X|X|X
-----
 |O|O
-----
 | | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 1
X|O| 
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X|O| 
-----
X| | 
-----
 | | 
Player O to 6
X|O| 
-----
X| | 
-----
O| | 
Player X to 4 for score 1
X|O| 
-----
X|X| 
-----
O| | 
Player O to 7
X|O| 
-----
X|X| 
-----
O|O| 
Player X to 5 for score 1
X|O| 
-----
X|X|X
-----
O|O| 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 1
X|O| 
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X|O| 
-----
X| | 
-----
 | | 
Player O to 7
X|O| 
-----
X| | 
-----
 |O| 
Player X to 6 for score 1
X|O| 
-----
X| | 
-----
X|O| 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 8
X| | 
-----
 | | 
-----
 | |O
Player X to 2 for score 1
X| |X
-----
 | | 
-----
 | |O
Player O to 3
X| |X
-----
O| | 
-

Player O to 4
X|X| 
-----
O|O| 
-----
 | | 
Player X to 2 for score 1
X|X|X
-----
O|O| 
-----
 | | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 8
X| | 
-----
 | | 
-----
 | |O
Player X to 2 for score 1
X| |X
-----
 | | 
-----
 | |O
Player O to 1
X|O|X
-----
 | | 
-----
 | |O
Player X to 6 for score 1
X|O|X
-----
 | | 
-----
X| |O
Player O to 7
X|O|X
-----
 | | 
-----
X|O|O
Player X to 3 for score 1
X|O|X
-----
X| | 
-----
X|O|O



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 1
X|O| 
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X|O| 
-----
X| | 
-----
 | | 
Player O to 6
X|O| 
-----
X| | 
-----
O| | 
Player X to 4 for score 1
X|O| 
-----
X|X| 
-----
O| | 
Player O to 5
X|O| 
-----
X|X|O
-----
O| | 
Player X to 8 for score 1
X|O| 
-----
X|X|O
-----
O| |X



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 3
X| | 
-----
O| | 
-

Player O to 7
X|O| 
-----
X| | 
-----
 |O| 
Player X to 6 for score 1
X|O| 
-----
X| | 
-----
X|O| 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 3
X| | 
-----
O| | 
-----
 | | 
Player X to 1 for score 1
X|X| 
-----
O| | 
-----
 | | 
Player O to 7
X|X| 
-----
O| | 
-----
 |O| 
Player X to 2 for score 1
X|X|X
-----
O| | 
-----
 |O| 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 3
X| | 
-----
O| | 
-----
 | | 
Player X to 1 for score 1
X|X| 
-----
O| | 
-----
 | | 
Player O to 4
X|X| 
-----
O|O| 
-----
 | | 
Player X to 2 for score 1
X|X|X
-----
O|O| 
-----
 | | 



 | | 
-----
 | | 
-----
 | | 
Player X to 0 for score 1
X| | 
-----
 | | 
-----
 | | 
Player O to 1
X|O| 
-----
 | | 
-----
 | | 
Player X to 3 for score 1
X|O| 
-----
X| | 
-----
 | | 
Player O to 5
X|O| 
-----
X| |O
-----
 | | 
Player X to 6 for score 1
X|O| 
-----
X| |O
-----
X| | 



 | | 
-----
 | | 
-----
 | | 


# Second Game

### Connect-Three on a 4x5 Board

This game is water down version of $Connect Four$. The original form of the game is as described below: 

Connect Four is a two-player connection game in which the players first choose a color and then take turns dropping colored discs from the top into a seven-column, six-row vertically suspended grid. The pieces fall straight down, occupying the next available space within the column. The objective of the game is to be the first to form a horizontal, vertical, or diagonal line of four of one's own discs. Connect Four is a solved game. The first player can always win by playing the right moves.

Source - <a href="https://en.wikipedia.org/wiki/Connect_Four">Connect Four-Wikipedia</a>
<img src="https://upload.wikimedia.org/wikipedia/commons/a/ad/Connect_Four.gif">

In this version of the game, there are <i>4 rows and 5 columns</i>. The rules are almost same as above except instead of connectiing four discs, a player who connects three discs in a series wins the game. And the player who goes first is represented by <b>X</b> and the player who goes second is represented by an <b>O</b>.

The player <b>X</b> plays according to the moves returned by the <i>negamax</i> algorithm and the <i>opppent</i> plays any random move from all the moves available to him.

In [21]:
'''
The negamax() is same as the one provided in the Assignment
'''
def negamax(game, depthLeft):
    # If at terminal state or depth limit, return utility value and move None
    if game.isOver() or depthLeft == 0:
        return game.getUtility(), None
    # Find best move and its value from current state
    bestValue = -float('infinity')
    bestMove = None
    for move in game.getMoves():
        # Apply a move to current state
        game.makeMove(move)
        # Use depth-first search to find eventual utility value and back it up.
        #  Negate it because it will come back in context of next player
        value, _ = negamax(game, depthLeft-1)
        # Remove the move from current state, to prepare for trying a different move
        game.unmakeMove(move)
        if value is None:
            continue
        value = - value
        # If the value is infinity then even though its greater than bestValue but we do not consider as a valid score
        if value > bestValue and value != float('infinity'):
            # Value for this move is better than moves tried so far from this state.
            bestValue = value
            bestMove = move
    return bestValue, bestMove

In [22]:
'''
The code for Connect_3 class is also almost the same as the TTT class given in the assignment with some modifications in
some the methods which are described along the functions.

The board representation
[ 0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19]  The number represents the index.

--------------------------
|  0 |  1 |  2 |  3 |  4 |
--------------------------
|  5 |  6 |  7 |  8 |  9 |
--------------------------
| 10 | 11 | 12 | 13 | 14 |
--------------------------
| 15 | 16 | 17 | 18 | 19 |
--------------------------
This grid represents the actual location to which that index i in the list represents.
'''
from copy import copy

class Connect_3(object):

    def __init__(self):
        self.board = [' ']*20  # the board is represented as a single list of 20 element
        self.player = 'X'      # [' ',' ',' ',' ',' ',' ',' ',' ',' ',' ',' ',' ',' ',' ',' ',' ',' ',' ',' ',' ']
        if False:
            self.board = ['X', 'X', ' ', 'X', 'O', 'O', ' ', ' ', ' ']
            self.player = 'O'
        self.playerLookAHead = self.player
    '''
    The locatins() is based on the same concept as the previous one. It takes ' ' as a parameter to find the next possible moves.
    Since in Connect Four the discs are dropped from the top of the grid so we can play only either on top of another disc or at 
    the bottom of the grid. For example-
    --------------------------
    |  0 |  1 |  2 |  3 |  4 |            So for this given board, the valid moves available are
    --------------------------
    |  5 |  6 |  7 |  8 |  9 |            [ 15, 6, 12, 13, 19]. So for any given state there will   
    --------------------------
    | 10 |  O | 12 | 13 | 14 |            be at max 5 moves available.
    --------------------------
    | 15 |  X |  O |  X | 19 |
    --------------------------

    '''

    def locations(self, c):
        a = [i for i, mark in enumerate(self.board) if mark == c] # This collects all the locations of the character given
        if c != ' ':                                              # If the character is not ' ' then return the list as it is
            return a
        #print(a)                                                 # Otherwise, we need to find valid moves in case of ' ' 
        for i in range(3):                                        # The i value goes from rows [5..9],[10..14],[15..19] 
            for j in range(5):                                    # Whereas j goes from 0 to 4 in each row 
                if self.board[((i+1)*5)+j]==' ':                  # The logic is to check if there is a ' ' under a ' '
                    #print((i*5)+j)                               # if yes then remove that element from the list of ' 's. 
                    a.remove((i*5)+j)
        return a                                                  # This returns a list of ' ' positions which are valid moves
    
    def getMoves(self):
        moves = self.locations(' ')
        return moves

    def getUtility(self):
        whereX = self.locations('X')
        whereO = self.locations('O')
        wins = [[0, 1, 2], [1,2,3],[2,3, 4],                     # 
                [5,6,7], [6, 7, 8],[7,8,9],                      #  All horizontal combinations 
                [10,11,12], [11,12,13], [12,13,14],              #
                [15,16,17], [16,17,18],[17,18,19],               #
                [0,5,10],[5,10,15],                              ##
                [1,6,11],[6,11,16],                              ## All vertical combinations
                [2,7,12],[7,12,17],                              ##
                [3,8,13],[8,13,18],                              ##
                [4,9,14],[9,14,19],                              ##
                [5,11,17],[0,6,12],[6,12,18],[1,7,13],[7,13,19],[2,8,14],  ### All the diagonal combinations
                [2,6,10],[3,7,11],[7,11,15],[4,8,12],[8,12,16],[9,13,17]]  ###
        isXWon = any([all([wi in whereX for wi in w]) for w in wins])
        isOWon = any([all([wi in whereO for wi in w]) for w in wins])
        if isXWon:
            #print('won')
            return 1 if self.playerLookAHead is 'X' else -1
        elif isOWon:
            #print('lost')
            return 1 if self.playerLookAHead is 'O' else -1
        elif ' ' not in self.board:
            #print('draw')
            return 0
        else:
            #print('no move')
            return None  ########################################################## CHANGED FROM -0.1

    def isOver(self):
        return self.getUtility() is not None

    def makeMove(self, move):
        self.board[move] = self.playerLookAHead
        self.playerLookAHead = 'X' if self.playerLookAHead == 'O' else 'O'

    def changePlayer(self):
        self.player = 'X' if self.player == 'O' else 'O'
        self.playerLookAHead = self.player

    def unmakeMove(self, move):
        self.board[move] = ' '
        self.playerLookAHead = 'X' if self.playerLookAHead == 'O' else 'O'

    def __str__(self):
        s = '---------------------\n| {} | {} | {} | {} | {} |\n---------------------\n| {} | {} | {} | {} | {} |\n---------------------\n| {} | {} | {} | {} | {} |\n---------------------\n| {} | {} | {} | {} | {} |\n---------------------\n'.format(*self.board)
        return s

In [23]:
import random
def opponent(game):                                         # The oppenet uses Random move from all possible valid moves
    return random.choice(game.getMoves())

def playGame(game,opponent,depthLimit):
    print(game)
    while not game.isOver():
        score,move = negamax(game,depthLimit)
        if move == None :
            print('move is None. Stopping.')
            break
        game.makeMove(move)
        print('Player', game.player, 'to', move, 'for score' ,score)
        print(game)
        if not game.isOver():
            game.changePlayer()
            opponentMove = opponent(game)
            game.makeMove(opponentMove)
            print('Player', game.player, 'to', opponentMove)   ### FIXED ERROR IN THIS LINE!
            print(game)
            game.changePlayer()

In [24]:
game = Connect_3()
playGame(game,opponent,8)

---------------------
|   |   |   |   |   |
---------------------
|   |   |   |   |   |
---------------------
|   |   |   |   |   |
---------------------
|   |   |   |   |   |
---------------------

Player X to 17 for score 1
---------------------
|   |   |   |   |   |
---------------------
|   |   |   |   |   |
---------------------
|   |   |   |   |   |
---------------------
|   |   | X |   |   |
---------------------

Player O to 15
---------------------
|   |   |   |   |   |
---------------------
|   |   |   |   |   |
---------------------
|   |   |   |   |   |
---------------------
| O |   | X |   |   |
---------------------

Player X to 10 for score 1
---------------------
|   |   |   |   |   |
---------------------
|   |   |   |   |   |
---------------------
| X |   |   |   |   |
---------------------
| O |   | X |   |   |
---------------------

Player O to 5
---------------------
|   |   |   |   |   |
---------------------
| O |   |   |   |   |
---------------------
| X |   |  